In [1]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns

# Data Gathering

In [2]:
# df_fraud = pd.read_csv('data/Fraud Transaction Summary_Consolidated Expenses 2022 Q2.csv')
df_raw = pd.read_csv('data/all_expenses_as_of_11-22-2022.csv', low_memory=False)
df_IDs = pd.read_excel('data/Personal Airbnb ID.xlsx')
df_OM = pd.read_csv('data/Y20 _ CSQ 6E_HVR CONSULT (OM Responses) - Form Responses.csv')

# Cleaning

In [3]:
df_raw.shape

(99991, 77)

In [4]:
df_raw[df_raw.duplicated(keep=False)]

Name Region_Roster                Skill  \
1487          Aloyan, Rose Joy           NaN                   R2   
7572           Sajul, Jeibelle           NaN                   R2   
7598           Sajul, Jeibelle           NaN                   R2   
11090      De Leon, Tricia Mae          APAC                   R1   
25734    San Pedro, Dani Marie           NaN                   R1   
25988  Senerpida, Maria Isabel           NaN                   R2   
28709       Rabago, Gladys Mae           NaN                   R2   
28928       Rabago, Gladys Mae           NaN                   R2   
29572      De Leon, Tricia Mae          APAC                   R1   
29607           Amparo, Pamela          EMEA  Dedicated Superhost   
29623           Galang, Oliver          APAC  Dedicated Superhost   
29909           Galang, Oliver          APAC  Dedicated Superhost   
82755         Aloyan, Rose Joy           NaN                   R2   
88149    San Pedro, Dani Marie           NaN                   R1   
88150  Senerpida, Maria Isabel           NaN                   R2   
92227           Amparo, Pamela          EMEA  Dedicated Superhost   

          Team_Leader_Roster   Operations_Manager_Roster Site_Roster  \
1487   Lerio, Charmae Danica              Arellano, Joed        Cebu   
7572     Rivero, John Edward        Llauder, Ma Stenelli      Manila   
7598     Rivero, John Edward        Llauder, Ma Stenelli      Manila   
11090    David, John Maynard  Napeñas, Von Mychal Keaton      Manila   
25734           Barro, Joven              Arellano, Joed        Cebu   
25988    Toring, Christopher              Arellano, Joed        Cebu   
28709    Toring, Christopher              Arellano, Joed        Cebu   
28928    Toring, Christopher              Arellano, Joed        Cebu   
29572    David, John Maynard  Napeñas, Von Mychal Keaton      Manila   
29607   Hechanova, Cristline              Amplayo, Mariz      Manila   
29623          Guzon, Jerwin              Dulay, Donabel      Manila   
29909          Guzon, Jerwin              Dulay, Donabel      Manila   
82755  Lerio, Charmae Danica              Arellano, Joed        Cebu   
88149           Barro, Joven              Arellano, Joed        Cebu   
88150    Toring, Christopher              Arellano, Joed        Cebu   
92227   Hechanova, Cristline              Amplayo, Mariz      Manila   

                                       Role Resignation_LOA_Date  \
1487                            Team Leader                  NaN   
7572                     Team Leader Intern                  NaN   
7598                     Team Leader Intern                  NaN   
11090  Customer Experience Specialist (SME)                  NaN   
25734                           Team Leader                  NaN   
25988                           Team Leader                  NaN   
28709                           Team Leader                  NaN   
28928                           Team Leader                  NaN   
29572  Customer Experience Specialist (SME)                  NaN   
29607        Customer Experience Specialist                  NaN   
29623                           Team Leader                  NaN   
29909                           Team Leader                  NaN   
82755                           Team Leader                  NaN   
88149                           Team Leader                  NaN   
88150                           Team Leader                  NaN   
92227        Customer Experience Specialist                  NaN   

      t_activity_day t_expense_type  ... Scheduled_Status  Production_Status  \
1487      2022-08-10           Loss  ...           Active         Production   
7572      2022-04-05           Loss  ...           Active         Production   
7598      2022-04-05           Loss  ...           Active         Production   
11090     2022-05-27           Loss  ...           Active         Production   
25734     2022-03-28           Loss  ...           Active         Prod

In [5]:
df_raw = df_raw.drop_duplicates()

# Pre-processing

In [6]:
df_raw.columns

Index(['Name', 'Region_Roster', 'Skill', 'Team_Leader_Roster',
       'Operations_Manager_Roster', 'Site_Roster', 'Role',
       'Resignation_LOA_Date', 't_activity_day', 't_expense_type',
       't_lead_name', 't_id_airbnb_agent', 't_id_zendesk_agent',
       't_agent_name', 't_cost_center', 't_tier', 't_dim_ramp_status',
       't_tenure_in_organization', 't_tenure_in_sector', 't_ts_created_at',
       't_ds_created_at', 't_id_loss', 't_id_item', 't_id_coupon',
       't_id_coupon_code', 't_m_loss_amount_usd', 't_m_savings_native',
       't_m_savings_usd_at_issuance', 't_m_savings_usd_at_redemption',
       't_dim_native_currency', 't_id_customer',
       't_id_reservation_code_issued', 't_id_reservation_issued',
       't_id_ticket', 't_ticket_tier', 't_m_base_price_issued',
       't_m_extras_price_issued', 't_m_guest_fee', 't_m_host_fee',
       't_m_guest_paid', 't_m_host_received',
       't_m_full_resolution_time_in_minutes', 't_m_minutes_to_first_reply',
       't_dim_item_ty

In [7]:
#convert to datetime
df_raw['t_ts_created_at'] = pd.to_datetime(df_raw['t_ts_created_at'])
df_raw['t_activity_day'] = pd.to_datetime(df_raw['t_activity_day'])

#sort values
df_raw = df_raw.sort_values(by=['t_id_airbnb_agent', 't_ts_created_at'], ascending=True)

# Drop Duplicates

In [8]:
df_raw.drop_duplicates(keep='first', inplace=True)

In [9]:
df_raw.shape

(99983, 77)

In [10]:
!python --version

Python 3.9.12


# Modeling

In [11]:
df_raw.head(1)

Name Region_Roster Skill Team_Leader_Roster Operations_Manager_Roster  \
58222  NaN           NaN   NaN                NaN                       NaN   

      Site_Roster Role Resignation_LOA_Date t_activity_day t_expense_type  \
58222         NaN  NaN                  NaN     2022-09-30           Loss   

       ... Scheduled_Status  Production_Status  BCP_Status Roster_Channel  \
58222  ...              NaN                NaN         NaN            NaN   

      Week  Week_Start  Month_date   MMMYY Quarter  Year  
58222   40  2022-09-25  2022-10-01  Oct'22      Q4  2022  

[1 rows x 77 columns]

In [12]:
df_raw.shape

(99983, 77)

In [13]:
df_raw[~df_raw['t_m_loss_amount_usd'].isna()].shape

(64796, 77)

In [14]:
df_raw['t_m_savings_usd_at_issuance'].isna().sum()

64796

In [15]:
# sanity check
(df_raw['t_m_savings_usd_at_issuance'].isna().sum() 
 + df_raw['t_m_loss_amount_usd'].isna().sum()) == df_raw.shape[0]

True

In [16]:
df_raw.isna().sum()[:50]

Name                                     260
Region_Roster                          59612
Skill                                    260
Team_Leader_Roster                       260
Operations_Manager_Roster                260
Site_Roster                              260
Role                                     260
Resignation_LOA_Date                   96755
t_activity_day                             0
t_expense_type                             0
t_lead_name                                0
t_id_airbnb_agent                          0
t_id_zendesk_agent                         0
t_agent_name                               0
t_cost_center                              0
t_tier                                     0
t_dim_ramp_status                          0
t_tenure_in_organization                   0
t_tenure_in_sector                         0
t_ts_created_at                            0
t_ds_created_at                            0
t_id_loss                                  0
t_id_item 

In [17]:
# rule 1: customer and agent id are the same
df_raw['agent_customer_same'] = df_raw.apply(lambda x: (x['t_id_airbnb_agent']==x['t_id_customer']), axis=1).astype(int)

In [18]:
# rule 2: abnormal frequent transactions
df_freq = (df_raw.groupby(['t_id_airbnb_agent', 't_activity_day'])['t_expense_type'].count()
           ).rename('total_frequency').reset_index()
df_raw = df_raw.merge(df_freq, on=['t_id_airbnb_agent', 't_activity_day'])
print(df_freq['total_frequency'].quantile(0.9))

freq = df_freq['total_frequency'].quantile(0.9)
df_raw['abnormal_daily_frequency'] = df_raw['total_frequency'].apply(lambda x:(x >= freq).astype(int))

3.0


In [19]:
# rule 3: Shorter interval in between transactions per agent than normal
df_raw['time_diff_from_last_trans'] = df_raw.groupby('t_id_airbnb_agent')['t_ts_created_at'].apply(lambda x: x-x.shift(1))
# get the mean of each agent's time intervals per transaction
df_mean_time_diff = df_raw.groupby('t_id_airbnb_agent')['time_diff_from_last_trans'].mean().reset_index()
# get the 1st
print(df_mean_time_diff['time_diff_from_last_trans'].quantile(0.01))

def abnormal_short_interval_time(df_raw):
    """Return True if agent has been processing loss/coupon transaction
    in shorter intervals than the normal population.
    """
    agents_list = (df_mean_time_diff[(df_mean_time_diff['time_diff_from_last_trans']
                                    <= df_mean_time_diff['time_diff_from_last_trans']
                                    .quantile(0.01))]['t_id_airbnb_agent'].tolist())
    
    df_raw['abnormal_process_time_interval'] = (df_raw['t_id_airbnb_agent'].isin(agents_list)).astype(int)
    
    return df_raw

df_new = abnormal_short_interval_time(df_raw)

0 days 09:28:16.933414932


In [20]:
df_new.head(2)

Name Region_Roster Skill Team_Leader_Roster Operations_Manager_Roster  \
0  NaN           NaN   NaN                NaN                       NaN   
1  NaN           NaN   NaN                NaN                       NaN   

  Site_Roster Role Resignation_LOA_Date t_activity_day t_expense_type  ...  \
0         NaN  NaN                  NaN     2022-09-30           Loss  ...   
1         NaN  NaN                  NaN     2022-11-04         Coupon  ...   

   Week_Start  Month_date   MMMYY Quarter  Year agent_customer_same  \
0  2022-09-25  2022-10-01  Oct'22      Q4  2022                   0   
1  2022-10-30  2022-11-01  Nov'22      Q4  2022                   0   

  total_frequency abnormal_daily_frequency time_diff_from_last_trans  \
0               1                        0                       NaT   
1               1                        0          34 days 17:13:28   

  abnormal_process_time_interval  
0                              0  
1                              0  

[2 rows x 82 columns]

In [21]:
# rule 4: if `without reservation` for coupon related investments, prone to fraud

In [22]:
df_raw.columns

Index(['Name', 'Region_Roster', 'Skill', 'Team_Leader_Roster',
       'Operations_Manager_Roster', 'Site_Roster', 'Role',
       'Resignation_LOA_Date', 't_activity_day', 't_expense_type',
       't_lead_name', 't_id_airbnb_agent', 't_id_zendesk_agent',
       't_agent_name', 't_cost_center', 't_tier', 't_dim_ramp_status',
       't_tenure_in_organization', 't_tenure_in_sector', 't_ts_created_at',
       't_ds_created_at', 't_id_loss', 't_id_item', 't_id_coupon',
       't_id_coupon_code', 't_m_loss_amount_usd', 't_m_savings_native',
       't_m_savings_usd_at_issuance', 't_m_savings_usd_at_redemption',
       't_dim_native_currency', 't_id_customer',
       't_id_reservation_code_issued', 't_id_reservation_issued',
       't_id_ticket', 't_ticket_tier', 't_m_base_price_issued',
       't_m_extras_price_issued', 't_m_guest_fee', 't_m_host_fee',
       't_m_guest_paid', 't_m_host_received',
       't_m_full_resolution_time_in_minutes', 't_m_minutes_to_first_reply',
       't_dim_item_ty

In [23]:
# rule 5: suspicious duplicated ticket ID

cols = ['Name', 't_lead_name', 't_ts_created_at',
        't_id_reservation_code_issued', 't_id_reservation_issued',
        't_id_ticket', 't_expense_type', 't_m_loss_amount_usd',
        'With_Reservation', 't_id_airbnb_agent','t_id_customer',
        'abnormal_daily_frequency']


# remove Loss transactions with 0 USD
df_ = df_new[~(df_new['t_m_loss_amount_usd'] == 0)]
df = (df_[df_.duplicated(subset=['t_id_ticket'], keep=False)]
        .sort_values(by=['t_id_ticket', 't_ts_created_at']))[cols]
ticket_df = df.groupby(['t_id_ticket']).agg({'t_id_airbnb_agent': list,
                                             't_expense_type': list,
                                             't_m_loss_amount_usd': list,
                                             't_id_customer': list})
ticket_df.head(2)

t_id_airbnb_agent  t_expense_type t_m_loss_amount_usd  \
t_id_ticket                                                                 
2020023393508  [311958943, 311958943]  [Coupon, Loss]        [nan, 709.6]   
2020023622223  [407547719, 258699751]    [Loss, Loss]    [2720.47, 211.3]   

                        t_id_customer  
t_id_ticket                            
2020023393508      [2294656, 2294656]  
2020023622223  [365620364, 365620364]

In [24]:
# add new columns
ticket_df['num_unique_agent'] = ticket_df['t_id_airbnb_agent'].apply(lambda x: len(np.unique(x)))
ticket_df['num_of_transaction'] = ticket_df['t_expense_type'].apply(lambda x: len(x))
ticket_df['num_unique_customer'] = ticket_df['t_id_customer'].apply(lambda x: len(np.unique(x)))

# new column to flag suspicious transaction
ticket_df['suspicious_duplicates'] = np.nan

# columns to flag  LOSS investment
ticket_df['Loss'] = ticket_df['t_expense_type'].apply(lambda x: set(x).intersection(['Loss']))
ticket_df['is_Loss'] = (ticket_df['Loss'] == {'Loss'}).astype(int)

# columns to flag Coupon investment
ticket_df['Coupon'] = ticket_df['t_expense_type'].apply(lambda x: set(x).intersection(['Coupon']))
ticket_df['is_Coupon'] = (ticket_df['Coupon'] == {'Coupon'}).astype(int)

In [25]:
# legitimate case 1: coupon and loss given to only 1 customer
ticket_df.loc[(ticket_df['num_unique_customer'] == 1) &
              (ticket_df['num_of_transaction'] == 2) &
              (ticket_df['is_Coupon']==1) &
              (ticket_df['is_Loss']==1), 'suspicious_duplicates'] = 0

# legitimate case 2:loss or coupon given to guest and customer 
ticket_df.loc[(ticket_df['num_unique_customer'] == 2) &
              (ticket_df['num_of_transaction'] == 2), 'suspicious_duplicates'] = 0

# legitimate case 3: multiple agents in a same reservation/ticket with 1 or 2 customers (host or/and guest)
ticket_df.loc[(ticket_df['num_unique_agent'] > 1) &
          ((ticket_df['num_unique_customer']== 1) |
          (ticket_df['num_unique_customer']== 2)),'suspicious_duplicates'] = 0

# legitimate case 4: same agent processing to same customer not more than twice
ticket_df.loc[(ticket_df['suspicious_duplicates'].isna()) &
          (ticket_df['num_unique_agent'] == 1) &
          (ticket_df['num_unique_customer'] == 1) &
          (ticket_df['num_of_transaction'] < 3), 'suspicious_duplicates'] = 0

# legitimate case 5: same agent processing to same customer 3x.
# however, the investments are combinations of coupon and loss
ticket_df.loc[(ticket_df['suspicious_duplicates'].isna()) &
          (ticket_df['num_unique_agent'] == 1) &
          (ticket_df['num_unique_customer'] == 1) &
          (ticket_df['num_of_transaction'] == 3) &
          (ticket_df['is_Loss']==1) &
          (ticket_df['is_Coupon']==1), 'suspicious_duplicates'] = 0

# suspicious case 1: transactions for the same ticket were 3 or more
ticket_df.loc[(ticket_df['suspicious_duplicates'].isna()) &
          (ticket_df['num_unique_agent'] == 1) &
          (ticket_df['num_unique_customer'] == 1) &
          (ticket_df['num_of_transaction'] >= 3), 'suspicious_duplicates'] = 1

# suspicious case 2: more than 2 unique customers
ticket_df.loc[(ticket_df['suspicious_duplicates'].isna()) &
             (ticket_df['num_unique_customer'] > 2), 'suspicious_duplicates'] = 1

# suspicious case 3: 
# sample case: 2 unique customers but processed more than twice with no combination of coupon/loss
ticket_df.loc[ticket_df['suspicious_duplicates'].isna(), 'suspicious_duplicates'] = 1

In [26]:
ticket_df['suspicious_duplicates'].value_counts()

0.0    4300
1.0     144
Name: suspicious_duplicates, dtype: int64

In [27]:
duplicate_ticket_df = ticket_df.reset_index()[['t_id_ticket', 'suspicious_duplicates']]

In [28]:
df = df_new.merge(duplicate_ticket_df, on='t_id_ticket', how='left')
df.head(2)

Name Region_Roster Skill Team_Leader_Roster Operations_Manager_Roster  \
0  NaN           NaN   NaN                NaN                       NaN   
1  NaN           NaN   NaN                NaN                       NaN   

  Site_Roster Role Resignation_LOA_Date t_activity_day t_expense_type  ...  \
0         NaN  NaN                  NaN     2022-09-30           Loss  ...   
1         NaN  NaN                  NaN     2022-11-04         Coupon  ...   

   Month_date   MMMYY  Quarter  Year agent_customer_same total_frequency  \
0  2022-10-01  Oct'22       Q4  2022                   0               1   
1  2022-11-01  Nov'22       Q4  2022                   0               1   

  abnormal_daily_frequency time_diff_from_last_trans  \
0                        0                       NaT   
1                        0          34 days 17:13:28   

  abnormal_process_time_interval suspicious_duplicates  
0                              0                   NaN  
1                              0                   NaN  

[2 rows x 83 columns]

In [29]:
# fill transactions with no duplicate with 0
df['suspicious_duplicates'].fillna(0, inplace=True)

In [30]:
# rule 6: customer ID is one of the personal IDs of ABNB employees
df['t_id_customer'] = df['t_id_customer'].astype(str)
personal_abnb_ids = df_IDs[~df_IDs['id_airbnb_personal'].isna()
                          ]['id_airbnb_personal'].astype(int).astype(str).unique().tolist()
df['t_id_customer'] = df['t_id_customer'].astype(str)
df['personal_ID_recepient'] = df['t_id_customer'].isin(personal_abnb_ids).astype(int)
df['personal_ID_recepient'].value_counts()

0    99971
1       12
Name: personal_ID_recepient, dtype: int64

In [31]:
df[df['personal_ID_recepient'] == 1][['Name','t_expense_type', 't_m_loss_amount_usd', 't_m_savings_usd_at_issuance']]

Name t_expense_type  t_m_loss_amount_usd  \
46768            Arcega, John Marl         Coupon                  NaN   
46769            Arcega, John Marl           Loss            20.200000   
46938    Barreto, Nikki Antonnette           Loss            10.460000   
75838              Lopez, Richmond           Loss             2.360000   
78987               Tablo, Jocelyn           Loss            31.980000   
80143             Morata, Joselito           Loss           193.187399   
80857  Paracuelles, Michael Angelo           Loss             4.210000   
81571            Cayetano, Jhanine           Loss           195.020053   
83977       Macuno, Rochelle Joyce         Coupon                  NaN   
93058         Madlangbayan, Gloria         Coupon                  NaN   
93403        Abella, Princess Niña         Coupon                  NaN   
93553       Planteras, Razil Honey         Coupon                  NaN   

       t_m_savings_usd_at_issuance  
46768                    38.000000  
46769                          NaN  
46938                          NaN  
75838                          NaN  
78987                          NaN  
80143                          NaN  
80857                          NaN  
81571                          NaN  
83977                    34.856253  
93058                    26.408683  
93403                    60.000000  
93553                    25.816056

In [32]:
# Rule 7: 
# If amount above $3000 (loss/coupon) and not found in the list,then non-compliant

In [33]:
df_OM.shape

(3687, 37)

In [34]:
df_OM[~df_OM['Amount Approved in USD'].isna()].shape

(364, 37)

In [35]:
df_OM[~(df_OM['Ticket ID'].isna())].shape

(1669, 37)

In [36]:
df_masterfile_OM = df_OM[~(df_OM['Ticket ID'].isna())].sort_values('Ticket ID')

In [37]:
df_masterfile_OM['Ticket ID'] = df_masterfile_OM['Ticket ID'].astype(str)

In [38]:
ticketIds_reported = df_masterfile_OM['Ticket ID'].unique().tolist()

In [39]:
df['Loss'] = (df['t_expense_type'] == 'Loss').astype(int)
df['Coupon'] = (df['t_expense_type'] == 'Coupon').astype(int)

df['transaction_3000USD'] = 0 
df.loc[(df['Loss']==1) & (df['t_m_loss_amount_usd'] >= 3000),
       'transaction_3000USD'] = 1
df.loc[(df['Coupon']==1) & (df['t_m_savings_usd_at_issuance'] >= 3000),
       'transaction_3000USD'] = 1
df['t_id_ticket'] = df['t_id_ticket'].astype(str)

In [40]:
df['transaction_3000USD'].value_counts()

0    99857
1      126
Name: transaction_3000USD, dtype: int64

In [41]:
# Fraud
df['not_reported_3000USD'] = 0
df.loc[(df['transaction_3000USD']==1) & 
       (~df['t_id_ticket'].isin(ticketIds_reported)), 'not_reported_3000USD'] = 1

In [42]:
df[df['not_reported_3000USD']==1][['t_id_ticket', 't_activity_day', 'Name',
                                   't_lead_name','t_m_loss_amount_usd',
                                   't_m_savings_usd_at_issuance']]

t_id_ticket t_activity_day                        Name  \
3224   2020056338229     2022-09-22           Guzon, Cherry Ann   
4431   2020030102508     2022-02-04         Rivero, John Edward   
4433   2020032411542     2022-02-18         Rivero, John Edward   
6647   2020031725574     2022-02-21                         NaN   
8877   2020063361660     2022-11-10          Mosende, Ian Kevin   
8881   2020063823698     2022-11-17          Mosende, Ian Kevin   
17256  2020063271594     2022-11-16             Centino, Shella   
23720  2020064157817     2022-11-17          Daguitera, Charmel   
30852  2020035198142     2022-03-18  Gellecanao, Benjamin Andre   
30861  2020045209120     2022-06-14  Gellecanao, Benjamin Andre   
30868  2020050977988     2022-08-04  Gellecanao, Benjamin Andre   
30884  2020062726075     2022-11-21  Gellecanao, Benjamin Andre   
34998  2020057965173     2022-09-25               Butaya, Arnel   
41288  2020051506877     2022-08-04               Cuyos, Darryl   
42723  2020044139734     2022-06-04          Martin, Bailey Jed   
42751  2020049568277     2022-08-01          Martin, Bailey Jed   
42786  2020054949794     2022-09-02          Martin, Bailey Jed   
43191  2020037483663     2022-06-02               Yu, Cyman Tan   
43406  2020037959537     2022-04-14     Senerpida, Maria Isabel   
44656  2020033077859     2022-02-22                Barro, Joven   
44702  2020044152977     2022-06-08                Barro, Joven   
44704  2020044725272     2022-06-13                Barro, Joven   
44709  2020046094652     2022-06-22                Barro, Joven   
44710  2020046199780     2022-06-22                Barro, Joven   
44758  2020057991700     2022-10-11                Barro, Joven   
44761  2020058468004     2022-10-16                Barro, Joven   
44762  2020058727507     2022-10-16                Barro, Joven   
44766  2020053515151     2022-10-22                Barro, Joven   
44771  2020060009577     2022-10-31                Barro, Joven   
44782  2020063716405     2022-11-09                Barro, Joven   
44788  2020064440430     2022-11-16                Barro, Joven   
44789  2020063358184     2022-11-17                Barro, Joven   
50325  2020039557860     2022-04-27  Napeñas, Von Mychal Keaton   
50361  2020032202608     2022-02-15         Toring, Christopher   
50369  2020035001735     2022-03-17         Toring, Christopher   
50497  2020054605280     2022-09-04         Toring, Christopher   
50520  2020057939902     2022-10-03         Toring, Christopher   
50536  2020064582038     2022-11-17         Toring, Christopher   
51339  2020036006968     2022-04-01               Espago, Alvin   
51419  2020044910348     2022-06-17               Espago, Alvin   
51625  2020036826477     2022-04-07            Peralta, Kenneth   
61959  2020028804549     2022-01-14       Gazo, Florence Nadine   
90584  2020047802265     2022-08-03        Tapalla, Paul Edward   
93309  2020055394015     2022-09-06             Ras, Karl James   
95155  2020052449128     2022-08-11               Bianes, Jowin   
95310  2020053498275     2022-08-19           Diaz, Niguel John   
99754  2020053515151     2022-10-27             Paredes, Siaska   

               t_lead_name  t_m_loss_amount_usd  t_m_savings_usd_at_issuance  
3224      Allyssa Guevarra          3034.435875                          NaN  
4431   Ma Stenelli Llauder          3695.140000                          NaN  
4433   Ma Stenelli Llauder          7881.530000                          NaN  
6647      Daniel Dela Pena                  NaN                      20000.0  
8877           John Rivero          3329.140000                          NaN  
8881         Donabel Dulay          3659.144326                          NaN  
17256          Joven Barro          3042.290281                          NaN  
23720          Ian Mosende          4940.444259                          NaN  
30852        Joed Arellano                  NaN                       3000.0  
30

In [43]:
df[df['not_reported_3000USD']==1]['t_id_ticket'].nunique()

46

In [44]:
# checker
ids = df[df['not_reported_3000USD']==1]['t_id_ticket'].unique().tolist()
len(set(ids) - set(ticketIds_reported))

46

In [45]:
cols = ['t_ts_created_at', 't_id_reservation_code_issued',
        't_id_reservation_issued', 't_id_ticket', 't_expense_type',
        't_m_loss_amount_usd', 't_m_savings_usd_at_issuance', 'Name',
        't_id_airbnb_agent','t_id_customer',
        'With_Reservation', 'abnormal_daily_frequency', 'agent_customer_same',
        'abnormal_process_time_interval', 'suspicious_duplicates',
         'not_reported_3000USD', 'personal_ID_recepient', 'prediction_confidence']

# Rules

Labels for model output:
- 0 - Unlikely
- 1 - Likely
- 2 - Extremely Likely
- 3 - Certain

In [46]:
df['prediction_confidence'] = np.nan

## Certain (Label 3)

In [47]:
df.loc[df['agent_customer_same'] == 1, 'prediction_confidence'] = 3

In [48]:
df.loc[df['personal_ID_recepient'] == 1, 'prediction_confidence'] = 3

## Extremely Likely (Label 2)

In [49]:
df.loc[df['not_reported_3000USD']==1, 'prediction_confidence'] = 2

In [50]:
df[(df['t_id_reservation_code_issued'].isna()) &
   (df['With_Reservation'] == 0) &
   (df['abnormal_daily_frequency'] == 1) &
   (df['abnormal_process_time_interval'] == 1)]

Name Region_Roster                Skill  \
26336           Aloyan, Rose Joy           NaN                   R2   
33442  Zarate, Patricia Beatrice          EMEA  Dedicated Superhost   
33443  Zarate, Patricia Beatrice          EMEA  Dedicated Superhost   
33444  Zarate, Patricia Beatrice          EMEA  Dedicated Superhost   
33445  Zarate, Patricia Beatrice          EMEA  Dedicated Superhost   
33446  Zarate, Patricia Beatrice          EMEA  Dedicated Superhost   
79567             Lopez, Patrick          APAC   Cancellations Lite   
79568             Lopez, Patrick          APAC   Cancellations Lite   
79569             Lopez, Patrick          APAC   Cancellations Lite   
90630      Cayetano, Justine Mae           NaN                   R1   
90640      Cayetano, Justine Mae           NaN                   R1   
90641      Cayetano, Justine Mae           NaN                   R1   
90642      Cayetano, Justine Mae           NaN                   R1   
90643      Cayetano, Justine Mae           NaN                   R1   
90644      Cayetano, Justine Mae           NaN                   R1   
90645      Cayetano, Justine Mae           NaN                   R1   
90689      Cayetano, Justine Mae           NaN                   R1   
90690      Cayetano, Justine Mae           NaN                   R1   
90691      Cayetano, Justine Mae           NaN                   R1   
90692      Cayetano, Justine Mae           NaN                   R1   
90693      Cayetano, Justine Mae           NaN                   R1   
90713      Cayetano, Justine Mae           NaN                   R1   
90714      Cayetano, Justine Mae           NaN                   R1   
90715      Cayetano, Justine Mae           NaN                   R1   
90716      Cayetano, Justine Mae           NaN                   R1   
90717      Cayetano, Justine Mae           NaN                   R1   
90718      Cayetano, Justine Mae           NaN                   R1   
90719      Cayetano, Justine Mae           NaN                   R1   
90720      Cayetano, Justine Mae           NaN                   R1   
90721      Cayetano, Justine Mae           NaN                   R1   
90722      Cayetano, Justine Mae           NaN                   R1   
90779               Ramos, Joyce           NaN                   R1   
90780               Ramos, Joyce           NaN                   R1   
90781               Ramos, Joyce           NaN                   R1   
90782               Ramos, Joyce           NaN                   R1   

         Team_Leader_Roster Operations_Manager_Roster Site_Roster  \
26336   Toring, Christopher            Arellano, Joed        Cebu   
33442  Hechanova, Cristline      Llauder, Ma Stenelli      Manila   
33443  Hechanova, Cristline      Llauder, Ma Stenelli      Manila   
33444  Hechanova, Cristline      Llauder, Ma Stenelli      Manila   
33445  Hechanova, Cristline      Llauder, Ma Stenelli      Manila   
33446  Hechanova, Cristline      Llauder, Ma Stenelli      Manila   
79567  Orfanel, Joel Victor       Lozano, Jim Michael      Manila   
79568  Orfanel, Joel Victor       Lozano, Jim Michael      Manila   
79569  Orfanel, Joel Victor       Lozano, Jim Michael      Manila   
90630     Obando, Marc Meal              Consul, Xyza      Manila   
90640     Obando, Marc Meal              Consul, Xyza      Manila   
90641     Obando, Marc Meal              Consul, Xyza      Manila   
90642     Obando, Marc Meal              Consul, Xyza      Manila   
90643     Obando, Marc Meal              Consul, Xyza      Manila   
90644     Obando, Marc Meal              Consul, Xyza      Manila   
90645     Obando, Marc Meal              Consul, Xyza      Manila   
90689     Obando, Marc Meal              Consul, Xyza      Manila   
90690     Obando, Marc Meal              Consul, Xyza      Manila   
90691     Obando, Marc Meal              Consul, Xyza      Manila   
90692     Obando, Marc Meal              Consul, Xyza      Manila   
90693     Obando, Marc

In [51]:
# for coupon related transactions
df.loc[(df['t_id_reservation_code_issued'].isna()) &
   (df['With_Reservation'] == 0) &
   (df['abnormal_daily_frequency'] == 1) &
   (df['abnormal_process_time_interval'] == 1), 'prediction_confidence'] = 2

## Extremely Likely (Label 2)

In [52]:
df.loc[(df['prediction_confidence'].isna()) &
       (df['suspicious_duplicates']==1) &
       (df['abnormal_process_time_interval']==1) &
       (df['abnormal_daily_frequency']==1), 'prediction_confidence'] = 2

## Likely (Label 1)

In [53]:
df.loc[(df['prediction_confidence'].isna()) &
       (df['suspicious_duplicates']==1), 'prediction_confidence'] = 1

## Unlikely (Label 0)

In [54]:
df['prediction_confidence'].fillna(0, inplace=True)

# Model Output

In [55]:
df['prediction_confidence'].value_counts()

0.0    99303
1.0      495
2.0      121
3.0       64
Name: prediction_confidence, dtype: int64

In [56]:
id_certain = df[df['prediction_confidence'] == 3]['t_id_ticket'].unique()
id_extreme_likely = df[df['prediction_confidence'] == 2]['t_id_ticket'].unique()
id_likely = df[df['prediction_confidence'] == 1]['t_id_ticket'].unique()

In [57]:
# certainly fraud
for i in id_certain[:20]:
    print('Predicted as Certainly Fraudulent with ticket ID: ', i)
    display(df[df['t_id_ticket'] == i][cols])

Predicted as Certainly Fraudulent with ticket ID:  2020044491090


t_ts_created_at t_id_reservation_code_issued  \
33448 2022-06-07 08:05:00+00:00                          NaN   

       t_id_reservation_issued    t_id_ticket t_expense_type  \
33448             4.748395e+09  2020044491090           Loss   

       t_m_loss_amount_usd  t_m_savings_usd_at_issuance  \
33448                189.0                          NaN   

                            Name  t_id_airbnb_agent t_id_customer  \
33448  Zarate, Patricia Beatrice          271203408     271203408   

       With_Reservation  abnormal_daily_frequency  agent_customer_same  \
33448                 1                         1                    1   

       abnormal_process_time_interval  suspicious_duplicates  \
33448                               1                    0.0   

       not_reported_3000USD  personal_ID_recepient  prediction_confidence  
33448                     0                      0                    3.0

Predicted as Certainly Fraudulent with ticket ID:  2020044492330


t_ts_created_at t_id_reservation_code_issued  \
33449 2022-06-07 08:27:00+00:00                          NaN   
33450 2022-06-07 08:27:00+00:00                          NaN   
33451 2022-06-07 08:29:00+00:00                          NaN   

       t_id_reservation_issued    t_id_ticket t_expense_type  \
33449             4.748430e+09  2020044492330           Loss   
33450             4.748426e+09  2020044492330           Loss   
33451             4.748434e+09  2020044492330           Loss   

       t_m_loss_amount_usd  t_m_savings_usd_at_issuance  \
33449                189.0                          NaN   
33450                189.0                          NaN   
33451                189.0                          NaN   

                            Name  t_id_airbnb_agent t_id_customer  \
33449  Zarate, Patricia Beatrice          271203408     271203408   
33450  Zarate, Patricia Beatrice          271203408     271203408   
33451  Zarate, Patricia Beatrice          271203408     271203408   

       With_Reservation  abnormal_daily_frequency  agent_customer_same  \
33449                 1                         1                    1   
33450                 1                         1                    1   
33451                 1                         1                    1   

       abnormal_process_time_interval  suspicious_duplicates  \
33449                               1                    1.0   
33450                               1                    1.0   
33451                               1                    1.0   

       not_reported_3000USD  personal_ID_recepient  prediction_confidence  
33449                     0                      0                    3.0  
33450                     0                      0                    3.0  
33451                     0                      0                    3.0

Predicted as Certainly Fraudulent with ticket ID:  2020044498479


...

t_ts_created_at t_id_reservation_code_issued  \
93058 2022-09-11 08:28:41+00:00                          NaN   

       t_id_reservation_issued    t_id_ticket t_expense_type  \
93058                      NaN  2020056448030         Coupon   

       t_m_loss_amount_usd  t_m_savings_usd_at_issuance                  Name  \
93058                  NaN                    26.408683  Madlangbayan, Gloria   

       t_id_airbnb_agent t_id_customer  With_Reservation  \
93058          463322818     335760267                 0   

       abnormal_daily_frequency  agent_customer_same  \
93058                         0                    0   

       abnormal_process_time_interval  suspicious_duplicates  \
93058                               0                    0.0   

       not_reported_3000USD  personal_ID_recepient  prediction_confidence  
93058                     0                      1                    3.0

Predicted as Certainly Fraudulent with ticket ID:  2020064299132


t_ts_created_at t_id_reservation_code_issued  \
93403 2022-11-16 14:13:10+00:00                   HM28BMDPHR   

       t_id_reservation_issued    t_id_ticket t_expense_type  \
93403             4.961422e+09  2020064299132         Coupon   

       t_m_loss_amount_usd  t_m_savings_usd_at_issuance  \
93403                  NaN                         60.0   

                        Name  t_id_airbnb_agent t_id_customer  \
93403  Abella, Princess Niña          464555909     451242051   

       With_Reservation  abnormal_daily_frequency  agent_customer_same  \
93403                 1                         0                    0   

       abnormal_process_time_interval  suspicious_duplicates  \
93403                               0                    0.0   

       not_reported_3000USD  personal_ID_recepient  prediction_confidence  
93403                     0                      1                    3.0

Predicted as Certainly Fraudulent with ticket ID:  2020062566332


t_ts_created_at t_id_reservation_code_issued  \
93553 2022-10-31 15:37:46+00:00                   HMQ2EZFYPD   

       t_id_reservation_issued    t_id_ticket t_expense_type  \
93553             4.952219e+09  2020062566332         Coupon   

       t_m_loss_amount_usd  t_m_savings_usd_at_issuance  \
93553                  NaN                    25.816056   

                         Name  t_id_airbnb_agent t_id_customer  \
93553  Planteras, Razil Honey          464557087     335760267   

       With_Reservation  abnormal_daily_frequency  agent_customer_same  \
93553                 1                         0                    0   

       abnormal_process_time_interval  suspicious_duplicates  \
93553                               0                    0.0   

       not_reported_3000USD  personal_ID_recepient  prediction_confidence  
93553                     0                      1                    3.0

In [58]:
# extremely likely as fraudulent
for i in id_extreme_likely[:5]:
    print('Predicted as Extremely Likely Fraudulent with ticket ID: ', i)
    display(df[df['t_id_ticket'] == i][cols])

Predicted as Extremely Likely Fraudulent with ticket ID:  2020056338229


t_ts_created_at t_id_reservation_code_issued  \
3224 2022-09-22 07:56:51+00:00                   HMWC89XFBT   

      t_id_reservation_issued    t_id_ticket t_expense_type  \
3224             4.874648e+09  2020056338229           Loss   

      t_m_loss_amount_usd  t_m_savings_usd_at_issuance               Name  \
3224          3034.435875                          NaN  Guzon, Cherry Ann   

      t_id_airbnb_agent t_id_customer  With_Reservation  \
3224          128313124        143874                 1   

      abnormal_daily_frequency  agent_customer_same  \
3224                         0                    0   

      abnormal_process_time_interval  suspicious_duplicates  \
3224                               0                    0.0   

      not_reported_3000USD  personal_ID_recepient  prediction_confidence  
3224                     1                      0                    2.0

Predicted as Extremely Likely Fraudulent with ticket ID:  2020030102508


t_ts_created_at t_id_reservation_code_issued  \
4431 2022-02-04 15:42:00+00:00                   HMRPPJ34JZ   

      t_id_reservation_issued    t_id_ticket t_expense_type  \
4431             4.111300e+09  2020030102508           Loss   

      t_m_loss_amount_usd  t_m_savings_usd_at_issuance                 Name  \
4431              3695.14                          NaN  Rivero, John Edward   

      t_id_airbnb_agent t_id_customer  With_Reservation  \
4431          134610421     328246595                 1   

      abnormal_daily_frequency  agent_customer_same  \
4431                         0                    0   

      abnormal_process_time_interval  suspicious_duplicates  \
4431                               0                    0.0   

      not_reported_3000USD  personal_ID_recepient  prediction_confidence  
4431                     1                      0                    2.0

Predicted as Extremely Likely Fraudulent with ticket ID:  2020032411542


t_ts_created_at t_id_reservation_code_issued  \
4433 2022-02-18 17:21:00+00:00                   HM2FATCFWJ   

      t_id_reservation_issued    t_id_ticket t_expense_type  \
4433             4.185848e+09  2020032411542           Loss   

      t_m_loss_amount_usd  t_m_savings_usd_at_issuance                 Name  \
4433              7881.53                          NaN  Rivero, John Edward   

      t_id_airbnb_agent t_id_customer  With_Reservation  \
4433          134610421      69855849                 1   

      abnormal_daily_frequency  agent_customer_same  \
4433                         0                    0   

      abnormal_process_time_interval  suspicious_duplicates  \
4433                               0                    0.0   

      not_reported_3000USD  personal_ID_recepient  prediction_confidence  
4433                     1                      0                    2.0

Predicted as Extremely Likely Fraudulent with ticket ID:  2020031725574


t_ts_created_at t_id_reservation_code_issued  \
6647 2022-02-21 08:55:00+00:00                          NaN   

      t_id_reservation_issued    t_id_ticket t_expense_type  \
6647                      NaN  2020031725574         Coupon   

      t_m_loss_amount_usd  t_m_savings_usd_at_issuance Name  \
6647                  NaN                      20000.0  NaN   

      t_id_airbnb_agent t_id_customer  With_Reservation  \
6647          149654085     126389654                 0   

      abnormal_daily_frequency  agent_customer_same  \
6647                         0                    0   

      abnormal_process_time_interval  suspicious_duplicates  \
6647                               0                    0.0   

      not_reported_3000USD  personal_ID_recepient  prediction_confidence  
6647                     1                      0                    2.0

Predicted as Extremely Likely Fraudulent with ticket ID:  2020063361660


t_ts_created_at t_id_reservation_code_issued  \
8877 2022-11-10 14:44:42+00:00                   HM3QFBQ3HB   

      t_id_reservation_issued    t_id_ticket t_expense_type  \
8877             4.922353e+09  2020063361660           Loss   

      t_m_loss_amount_usd  t_m_savings_usd_at_issuance                Name  \
8877              3329.14                          NaN  Mosende, Ian Kevin   

      t_id_airbnb_agent t_id_customer  With_Reservation  \
8877          176149408      25220673                 1   

      abnormal_daily_frequency  agent_customer_same  \
8877                         0                    0   

      abnormal_process_time_interval  suspicious_duplicates  \
8877                               0                    0.0   

      not_reported_3000USD  personal_ID_recepient  prediction_confidence  
8877                     1                      0                    2.0

In [59]:
# likely as fraudulent
for i in id_likely[:5]:
    print('Predicted as Likely Fraudulent with ticket ID: ', i)
    display(df[df['t_id_ticket'] == i][cols])

Predicted as Likely Fraudulent with ticket ID:  2020052936505


t_ts_created_at t_id_reservation_code_issued  \
485   2022-08-13 13:33:00+00:00                   HM3XYSNDXY   
49307 2022-08-20 09:48:00+00:00                   HM3XYSNDXY   
49308 2022-08-20 09:51:00+00:00                   HM3XYSNDXY   
49309 2022-08-20 09:52:00+00:00                   HM3XYSNDXY   
49310 2022-08-20 10:02:00+00:00                   HM3XYSNDXY   

       t_id_reservation_issued    t_id_ticket t_expense_type  \
485               4.908096e+09  2020052936505           Loss   
49307             4.908096e+09  2020052936505           Loss   
49308             4.908096e+09  2020052936505           Loss   
49309             4.908096e+09  2020052936505           Loss   
49310             4.908096e+09  2020052936505           Loss   

       t_m_loss_amount_usd  t_m_savings_usd_at_issuance  \
485                  40.20                          NaN   
49307                97.69                          NaN   
49308                71.56                          NaN   
49309                 1.19                          NaN   
49310                34.24                          NaN   

                        Name  t_id_airbnb_agent t_id_customer  \
485      Marbella, Jessanine          102420264     471333276   
49307  Gegrimal, Dan Michael          369252406      99234988   
49308  Gegrimal, Dan Michael          369252406     347560448   
49309  Gegrimal, Dan Michael          369252406     347560448   
49310  Gegrimal, Dan Michael          369252406     462417548   

       With_Reservation  abnormal_daily_frequency  agent_customer_same  \
485                   1                         0                    0   
49307                 1                         1                    0   
49308                 1                         1                    0   
49309                 1                         1                    0   
49310                 1                         1                    0   

       abnormal_process_time_interval  suspicious_duplicates  \
485                                 0                    1.0   
49307                               0                    1.0   
49308                               0                    1.0   
49309                               0                    1.0   
49310                               0                    1.0   

       not_reported_3000USD  personal_ID_recepient  prediction_confidence  
485                       0                      0                    1.0  
49307                     0                      0                    1.0  
49308                     0                      0                    1.0  
49309                     0                      0                    1.0  
49310                     0                      0                    1.0

Predicted as Likely Fraudulent with ticket ID:  2020042921916


t_ts_created_at t_id_reservation_code_issued  \
644 2022-05-27 12:20:00+00:00                   HMQWPHAQR4   
645 2022-05-27 12:20:00+00:00                   HMQWPHAQR4   
646 2022-05-27 12:20:00+00:00                   HMQWPHAQR4   
647 2022-05-27 12:32:00+00:00                   HMQWPHAQR4   
648 2022-05-27 12:33:00+00:00                   HMQWPHAQR4   

     t_id_reservation_issued    t_id_ticket t_expense_type  \
644             4.599037e+09  2020042921916         Coupon   
645             4.599037e+09  2020042921916           Loss   
646             4.599037e+09  2020042921916           Loss   
647             4.599037e+09  2020042921916           Loss   
648             4.599037e+09  2020042921916           Loss   

     t_m_loss_amount_usd  t_m_savings_usd_at_issuance                  Name  \
644                  NaN                         60.0  Hechanova, Cristline   
645               100.00                          NaN  Hechanova, Cristline   
646               121.08                          NaN  Hechanova, Cristline   
647               100.00                          NaN  Hechanova, Cristline   
648               100.76                          NaN  Hechanova, Cristline   

     t_id_airbnb_agent t_id_customer  With_Reservation  \
644          106740461     274364795                 1   
645          106740461     274364795                 1   
646          106740461     274364795                 1   
647          106740461     274364795                 1   
648          106740461     274364795                 1   

     abnormal_daily_frequency  agent_customer_same  \
644                         1                    0   
645                         1                    0   
646                         1                    0   
647                         1                    0   
648                         1                    0   

     abnormal_process_time_interval  suspicious_duplicates  \
644                               0                    1.0   
645                               0                    1.0   
646                               0                    1.0   
647                               0                    1.0   
648                               0                    1.0   

     not_reported_3000USD  personal_ID_recepient  prediction_confidence  
644                     0                      0                    1.0  
645                     0                      0                    1.0  
646                     0                      0                    1.0  
647                     0                      0                    1.0  
648                     0                      0                    1.0

Predicted as Likely Fraudulent with ticket ID:  2020028465835


t_ts_created_at t_id_reservation_code_issued  \
2108 2022-01-10 14:46:00+00:00                   HM4KNM3EER   
2119 2022-01-16 17:52:00+00:00                   HM4KNM3EER   
2120 2022-01-16 17:53:00+00:00                   HM4KNM3EER   

      t_id_reservation_issued    t_id_ticket t_expense_type  \
2108             3.986265e+09  2020028465835           Loss   
2119             3.986265e+09  2020028465835           Loss   
2120             3.986265e+09  2020028465835           Loss   

      t_m_loss_amount_usd  t_m_savings_usd_at_issuance                 Name  \
2108              1224.14                          NaN  Robles, Kate Zyrene   
2119              1049.54                          NaN  Robles, Kate Zyrene   
2120               966.12                          NaN  Robles, Kate Zyrene   

      t_id_airbnb_agent t_id_customer  With_Reservation  \
2108          127253421     222784296                 1   
2119          127253421     184170513                 1   
2120          127253421     156478693                 1   

      abnormal_daily_frequency  agent_customer_same  \
2108                         1                    0   
2119                         1                    0   
2120                         1                    0   

      abnormal_process_time_interval  suspicious_duplicates  \
2108                               0                    1.0   
2119                               0                    1.0   
2120                               0                    1.0   

      not_reported_3000USD  personal_ID_recepient  prediction_confidence  
2108                     0                      0                    1.0  
2119                     0                      0                    1.0  
2120                     0                      0                    1.0

Predicted as Likely Fraudulent with ticket ID:  2020028673048


t_ts_created_at t_id_reservation_code_issued  \
2118  2022-01-16 16:02:00+00:00                   HMJ5ZHS85N   
19840 2022-01-16 11:13:00+00:00                   HMJ5ZHS85N   
19841 2022-01-16 11:15:00+00:00                   HMJ5ZHS85N   

       t_id_reservation_issued    t_id_ticket t_expense_type  \
2118              4.165916e+09  2020028673048           Loss   
19840             4.165916e+09  2020028673048           Loss   
19841             4.165916e+09  2020028673048           Loss   

       t_m_loss_amount_usd  t_m_savings_usd_at_issuance                 Name  \
2118                 65.55                          NaN  Robles, Kate Zyrene   
19840               100.00                          NaN          Albea, Ryan   
19841                43.70                          NaN          Albea, Ryan   

       t_id_airbnb_agent t_id_customer  With_Reservation  \
2118           127253421     435200949                 1   
19840          252511305     298571726                 1   
19841          252511305     425951488                 1   

       abnormal_daily_frequency  agent_customer_same  \
2118                          1                    0   
19840                         1                    0   
19841                         1                    0   

       abnormal_process_time_interval  suspicious_duplicates  \
2118                                0                    1.0   
19840                               0                    1.0   
19841                               0                    1.0   

       not_reported_3000USD  personal_ID_recepient  prediction_confidence  
2118                      0                      0                    1.0  
19840                     0                      0                    1.0  
19841                     0                      0                    1.0

Predicted as Likely Fraudulent with ticket ID:  2020044783025


t_ts_created_at t_id_reservation_code_issued  \
3695  2022-06-17 00:01:00+00:00                   HM8FKKH824   
3696  2022-06-17 00:05:00+00:00                   HM8FKKH824   
14640 2022-06-16 23:14:00+00:00                   HM8FKKH824   
14641 2022-06-16 23:16:00+00:00                   HM8FKKH824   
14642 2022-06-16 23:18:00+00:00                   HM8FKKH824   
14643 2022-06-16 23:20:00+00:00                   HM8FKKH824   
14644 2022-06-16 23:21:00+00:00                   HM8FKKH824   
14645 2022-06-16 23:22:00+00:00                   HM8FKKH824   
14647 2022-06-21 02:05:00+00:00                   HM8FKKH824   

       t_id_reservation_issued    t_id_ticket t_expense_type  \
3695              4.726114e+09  2020044783025           Loss   
3696              4.726114e+09  2020044783025           Loss   
14640             4.726114e+09  2020044783025           Loss   
14641             4.726114e+09  2020044783025           Loss   
14642             4.726114e+09  2020044783025           Loss   
14643             4.726114e+09  2020044783025           Loss   
14644             4.726114e+09  2020044783025           Loss   
14645             4.726114e+09  2020044783025           Loss   
14647             4.726114e+09  2020044783025           Loss   

       t_m_loss_amount_usd  t_m_savings_usd_at_issuance                Name  \
3695                 210.0                          NaN          Lim, Jaime   
3696                 369.8                          NaN          Lim, Jaime   
14640                199.4                          NaN  Vallecera, Kenneth   
14641                198.0                          NaN  Vallecera, Kenneth   
14642                132.8                          NaN  Vallecera, Kenneth   
14643                 65.0                          NaN  Vallecera, Kenneth   
14644                195.0                          NaN  Vallecera, Kenneth   
14645                 70.0                          NaN  Vallecera, Kenneth   
14647                195.0                          NaN  Vallecera, Kenneth   

       t_id_airbnb_agent t_id_customer  With_Reservation  \
3695           131372703     186772660                 1   
3696           131372703     425237343                 1   
14640          218850631        822796                 1   
14641          218850631     462016511                 1   
14642          218850631     221390695                 1   
14643          218850631     462275098                 1   
14644          218850631     412748858                 1   
14645          218850631     352192895                 1   
14647          218850631     412748858                 1   

       abnormal_daily_frequency  agent_customer_same  \
3695                          1                    0   
3696                          1                    0   
14640                         1                    0   
14641                         1                    0   
14642                         1                    0   
14643                         1                    0   
14644                         1                    0   
14645                         1                    0   
14647                         0                    0   

       abnormal_process_time_interval  suspicious_duplicates  \
3695                                0                    1.0   
3696                                0                    1.0   
14640                               0                    1.0   
14641                               0                    1.0   
14642                               0                    1.0   
14643                               0                    1.0   
14644                               0                    1.0   
14645                               0                    1.0   
14647                               0                    1.0   

       not_reported_3000USD  personal_ID_recepient  prediction_confidence  
3695                      0                      0              

In [60]:
df['prediction_confidence'].value_counts()

0.0    99303
1.0      495
2.0      121
3.0       64
Name: prediction_confidence, dtype: int64

In [61]:
df[df['prediction_confidence'].isin([1,2,3])].shape

(680, 89)

Add rules:
- exclusivisity of agent-customer
- ratio of loss amount and reservation amount

*Fraud Prevention*
- low productivity
- attendance issues
- heartbeat (browsing activity)

In [62]:
df_customer_agg = df_new.groupby(['t_id_customer']).agg({'t_id_airbnb_agent':list, 't_ts_created_at':list,
                                                         't_m_loss_amount_usd': list,
                                                         't_expense_type': list,
                                                         't_id_ticket': list,
                                                         't_id_reservation_issued': list})

df_customer_agg['transaction_count'] = df_customer_agg['t_id_airbnb_agent'].apply(lambda x: len(x))
df_customer_agg['num_unique_agent'] = df_customer_agg['t_id_airbnb_agent'].apply(lambda x: len(np.unique(x)))
df_customer_agg['reservation_count'] = df_customer_agg['t_id_reservation_issued'].apply(lambda x: len(np.unique(x)))
df_customer_agg['ticket_count'] = df_customer_agg['t_id_ticket'].apply(lambda x: len(np.unique(x)))

In [63]:
df_customer_agg['transaction_count'].describe()

count    83372.000000
mean         1.199240
std         35.308403
min          1.000000
25%          1.000000
50%          1.000000
75%          1.000000
max      10195.000000
Name: transaction_count, dtype: float64

In [64]:
df_customer_agg['reservation_count'].describe()

count    83372.000000
mean         1.143957
std         34.219728
min          1.000000
25%          1.000000
50%          1.000000
75%          1.000000
max       9881.000000
Name: reservation_count, dtype: float64

In [65]:
df_customer_agg[(df_customer_agg['reservation_count'] > 1) &
                (df_customer_agg['ticket_count'] > 1) &
                 (df_customer_agg['num_unique_agent'] == 1)].shape

(95, 10)

In [66]:
df_customer_agg[(df_customer_agg['reservation_count'] > 1) &
                 (df_customer_agg['ticket_count'] > 1) &
                 (df_customer_agg['num_unique_agent'] == 1)]

t_id_airbnb_agent  \
t_id_customer                                                      
760849                                    [245247655, 245247655]   
2325684                                   [266136935, 266136935]   
4145741                                   [234657048, 234657048]   
4149897                                   [341741435, 341741435]   
5463516                                   [355697885, 355697885]   
...                                                          ...   
475979131      [458747481, 458747481, 458747481, 458747481, 4...   
482124624                                 [278142673, 278142673]   
483459259                                 [398840672, 398840672]   
484700390                                 [434619403, 434619403]   
487246423      [449803028, 449803028, 449803028, 449803028, 4...   

                                                 t_ts_created_at  \
t_id_customer                                                      
760849         [2022-09-23 06:03:26+00:00, 2022-09-23 06:04:3...   
2325684        [2022-09-10 21:44:59+00:00, 2022-10-21 19:40:3...   
4145741        [2022-10-08 13:27:52+00:00, 2022-10-08 13:33:0...   
4149897        [2022-03-30 01:00:00+00:00, 2022-03-30 01:43:0...   
5463516        [2022-10-09 20:10:30+00:00, 2022-10-12 13:11:1...   
...                                                          ...   
475979131      [2022-08-29 04:05:44+00:00, 2022-08-30 04:04:4...   
482124624      [2022-11-01 16:40:33+00:00, 2022-11-01 16:49:4...   
483459259      [2022-11-21 16:57:15+00:00, 2022-11-21 16:58:1...   
484700390      [2022-10-23 11:24:38+00:00, 2022-10-28 04:17:2...   
487246423      [2022-11-11 08:14:26+00:00, 2022-11-11 08:14:4...   

                                             t_m_loss_amount_usd  \
t_id_customer                                                      
760849                      [91.4532756900565, 41.5918590867814]   
2325684                                           [150.0, 150.0]   
4145741                      [38.544132482346, 84.0200161807449]   
4149897                                           [300.0, 110.4]   
5463516                     [55.1571980143408, 39.1937838658788]   
...                                                          ...   
475979131      [nan, nan, nan, nan, nan, nan, nan, nan, nan, ...   
482124624                                           [70.0, 70.0]   
483459259                   [123.413983392003, 57.5423655666484]   
484700390                                             [nan, nan]   
487246423      [nan, nan, nan, nan, nan, nan, nan, nan, nan, ...   

                                                  t_expense_type  \
t_id_customer                                                      
760849                                              [Loss, Loss]   
2325684                                             [Loss, Loss]   
4145741                                             [Loss, Loss]   
4149897                                             [Loss, Loss]   
5463516                                             [Loss, Loss]   
...                                                          ...   
475979131      [Coupon, Coupon, Coupon, Coupon, Coupon, Coupo...   
482124624                                           [Loss, Loss]   
483459259                                           [Loss, Loss]   
484700390                                       [Coupon, Coupon]   
487246423      [Coupon, Coupon, Coupon, Coupon, Coupon, Coupo...   

                                                     t_id_ticket  \
t_id_customer                                                      
760849                            [2020057555218, 2020057555188]   
2325684                           [2020056083558, 2020060814174]   
4145741                           [2020059524018, 2020059524819]   
4149897                           [2020035395408, 2020034577845]   
5463516                           [2020059769754, 2020059769668]   
...                            

**Using this rule, we capture customer-agent interaction within small time period. It seems legit and not fraudulent.**

In [67]:
# [agent-customer] pair interaction within the weeks
# [agent-customer] pair interaction within unique reservation

## New rule: Agent-customer exclusivity

In [68]:
df_copy = df.sort_values(by = ['t_id_customer', 't_ts_created_at'], ascending=True)[cols]
# dummy variable to rank or count transaction
df_copy['transaction'] = 1

df_copy = (df_copy.set_index('t_ts_created_at').groupby(['t_id_customer', 't_id_airbnb_agent'])
                                               .rolling("1d")['transaction']
                                               .sum().reset_index())

# customer-agent interaction per week
df_duplicates_week = df_copy[df_copy[['t_id_customer','t_id_airbnb_agent',
                                      'transaction']].duplicated(keep=False)]

## Flag as suspicious when customer and agent are interacting more than thrice in a day

In [69]:
# get agent-customer pair with at least 2 weeks interaction/transaction
agent_customer_df = (df_duplicates_week.groupby(['t_id_customer',
                                        't_id_airbnb_agent'])['t_ts_created_at']
                                       .agg(list).reset_index())

agent_customer_df['total_days'] = agent_customer_df['t_ts_created_at'].apply(lambda x: len(x))
# customers_id = agent_customer_df[agent_customer_df['total_days'] >= 1]['t_id_customer'].unique().tolist()

In [70]:
df_customer_agg = df.groupby('t_id_customer').agg({'t_id_ticket': list,
                                                   't_id_airbnb_agent' : list,
                                                   't_id_reservation_issued' : list})

In [71]:
df_customer_agg['num_unique_agent'] = df_customer_agg['t_id_airbnb_agent'].apply(lambda x: len(np.unique(x)))
df_customer_agg['reservation_count'] = df_customer_agg['t_id_reservation_issued'].apply(lambda x: len(x))
df_customer_agg['ticket_count'] = df_customer_agg['t_id_ticket'].apply(lambda x: len(x))

In [72]:
df_customer_agg.reset_index(inplace=True)

In [73]:
df_customer_agg[df_customer_agg['t_id_customer'] =='487246423']

t_id_customer                                        t_id_ticket  \
70057     487246423  [2020064005443, 2020064005443, 2020064005443, ...   

                                       t_id_airbnb_agent  \
70057  [449803028, 449803028, 449803028, 449803028, 4...   

                                 t_id_reservation_issued  num_unique_agent  \
70057  [4969520743.0, 4969520743.0, 4969520743.0, 496...                 1   

       reservation_count  ticket_count  
70057                 22            22

In [74]:
df_customer_agg['num_unique_agent'].describe()

count    83372.000000
mean         1.057849
std          5.048003
min          1.000000
25%          1.000000
50%          1.000000
75%          1.000000
max       1456.000000
Name: num_unique_agent, dtype: float64

In [75]:
df_customer_agg['num_unique_agent'].quantile(q=np.arange(0.95,1,0.01))

0.95       1.0
0.96       1.0
0.97       2.0
0.98       2.0
0.99       2.0
1.00    1456.0
Name: num_unique_agent, dtype: float64

In [76]:
df_customer_agg['reservation_count'].describe()

count    83372.000000
mean         1.199240
std         35.308403
min          1.000000
25%          1.000000
50%          1.000000
75%          1.000000
max      10195.000000
Name: reservation_count, dtype: float64

In [77]:
df_customer_agg[(df_customer_agg['num_unique_agent'] == 1)]['reservation_count'].describe()

count    80628.000000
mean         1.032941
std          0.327249
min          1.000000
25%          1.000000
50%          1.000000
75%          1.000000
max         54.000000
Name: reservation_count, dtype: float64

In [78]:
df_customer_agg[(df_customer_agg['num_unique_agent'] == 1)]['reservation_count'].quantile(q=np.arange(0.95,1,0.01))

0.95     1.0
0.96     1.0
0.97     1.0
0.98     2.0
0.99     2.0
1.00    54.0
Name: reservation_count, dtype: float64

In [79]:
customer_suspicious = (df_customer_agg[(df_customer_agg['num_unique_agent'] == 1) &
                                       (df_customer_agg['reservation_count'] >= 3)]
                                      ['t_id_customer'].tolist())
print(len(customer_suspicious))

df['suspicious_customer'] = df['t_id_customer'].isin(customer_suspicious).astype(int)

115


In [80]:
df['suspicious_customer'].value_counts()

0    99478
1      505
Name: suspicious_customer, dtype: int64

In [81]:
cols = ['t_ts_created_at', 't_id_reservation_code_issued',
        't_id_reservation_issued', 't_id_ticket', 't_expense_type',
        't_m_loss_amount_usd', 't_m_savings_usd_at_issuance', 'Name',
        't_id_airbnb_agent','t_id_customer',
        'With_Reservation', 'abnormal_daily_frequency', 'agent_customer_same',
        'abnormal_process_time_interval', 'suspicious_duplicates',
        'not_reported_3000USD', 'personal_ID_recepient','suspicious_customer',
        'prediction_confidence']

In [82]:
df.loc[(df['suspicious_customer']==1), 'prediction_confidence'] = 2

In [83]:
df['prediction_confidence'].value_counts()

0.0    99101
2.0      566
1.0      302
3.0       14
Name: prediction_confidence, dtype: int64

In [84]:
df['prediction_confidence'].value_counts(normalize=True)

0.0    0.991179
2.0    0.005661
1.0    0.003021
3.0    0.000140
Name: prediction_confidence, dtype: float64

In [85]:
df.shape

(99983, 90)

In [86]:
df_suspicious = df[df['prediction_confidence'].isin([1,2,3])]
df_suspicious.to_csv('predicted_suspicious_expenses_2022_updated.csv')

In [88]:
df.to_csv('transactions_2022.csv')

In [87]:
df_suspicious[df_suspicious['Name']=='Cayetano, Jhanine'].shape

(28, 90)

In [88]:
df[df['not_reported_3000USD']==1][cols]

t_ts_created_at t_id_reservation_code_issued  \
3224  2022-09-22 07:56:51+00:00                   HMWC89XFBT   
4431  2022-02-04 15:42:00+00:00                   HMRPPJ34JZ   
4433  2022-02-18 17:21:00+00:00                   HM2FATCFWJ   
6647  2022-02-21 08:55:00+00:00                          NaN   
8877  2022-11-10 14:44:42+00:00                   HM3QFBQ3HB   
8881  2022-11-17 21:18:50+00:00                   HM292K84X4   
17256 2022-11-16 20:08:26+00:00                   HMXPR4CHWT   
23720 2022-11-17 18:28:13+00:00                   HMZ49KZ9FW   
30852 2022-03-18 03:46:00+00:00                   HM3PYFWTNK   
30861 2022-06-14 12:01:00+00:00                   HM4SMJRCAD   
30868 2022-08-04 02:26:00+00:00                   HM989P33CZ   
30884 2022-11-21 18:29:04+00:00                   HMN5DD2SM3   
34998 2022-09-25 14:27:20+00:00                   HMBZNYP9XF   
41288 2022-08-04 03:02:00+00:00                   HMK2Q45ZFW   
42723 2022-06-04 14:28:00+00:00                   HMMNM2HKW5   
42751 2022-08-01 19:11:00+00:00                   HMF3FQKRZ4   
42786 2022-09-02 20:25:11+00:00                   HM4FJMNN8H   
43191 2022-06-02 13:42:00+00:00                   HM24QMRFXZ   
43406 2022-04-14 00:37:00+00:00                   HMBECA8F3S   
44656 2022-02-22 16:50:00+00:00                   HM93SJHYX4   
44702 2022-06-08 15:33:00+00:00                   HM4DPDPKPS   
44704 2022-06-13 15:19:00+00:00                   HMXY5Z3ACQ   
44709 2022-06-22 15:54:00+00:00                   HMYXHE5NYP   
44710 2022-06-22 22:38:00+00:00                   HM8ZTHQ2E2   
44758 2022-10-11 21:45:35+00:00                   HMJEFRTZQ5   
44761 2022-10-16 14:03:15+00:00                   HMMFTM85PQ   
44762 2022-10-16 14:03:51+00:00                   HMTYYHJPXW   
44766 2022-10-22 01:31:17+00:00                   HMN4DCENPF   
44771 2022-10-31 16:56:55+00:00                   HMA4FECDES   
44782 2022-11-09 15:41:44+00:00                   HM38SAKXM4   
44788 2022-11-16 21:54:05+00:00                   HM2AR5BPNR   
44789 2022-11-17 00:24:28+00:00                   HMYTHM8YQP   
50325 2022-04-27 15:03:00+00:00                   HMQZR4AQSY   
50361 2022-02-15 03:12:00+00:00                   HMNBYTP4F8   
50369 2022-03-17 08:38:00+00:00                   HMCH53CMMK   
50497 2022-09-04 19:28:51+00:00                   HMNZXCERQF   
50520 2022-10-03 21:11:59+00:00                   HM2DDAHJ4W   
50536 2022-11-17 16:34:45+00:00                   HMX8J5TJSM   
51339 2022-04-01 14:06:00+00:00                   HMQWJ4EEQ4   
51419 2022-06-17 07:48:00+00:00                   HM35CDAW4R   
51625 2022-04-07 11:40:00+00:00                   HMMS4XDN4X   
61959 2022-01-14 20:41:00+00:00                   HMARDSXRW9   
90584 2022-08-03 10:57:00+00:00                   HM5A4JCZDZ   
93309 2022-09-06 22:58:00+00:00                   HMAKFH3S3S   
95155 2022-08-11 09:33:00+00:00                   HM34JJQHWF   
95310 2022-08-19 13:20:00+00:00                   HMPWPS4MPF   
99754 2022-10-27 18:55:02+00:00                   HMN4DCENPF   

       t_id_reservation_issued    t_id_ticket t_expense_type  \
3224              4.874648e+09  2020056338229           Loss   
4431              4.111300e+09  2020030102508           Loss   
4433              4.185848e+09  2020032411542           Loss   
6647                       NaN  2020031725574         Coupon   
8877              4.922353e+09  2020063361660           Loss   
8881              3.785978e+09  2020063823698           Loss   
17256             4.964340e+09  2020063271594           Loss   
23720             4.814648e+09  2020064157817           Loss   
30852             4.315543e+09  2020035198142         Coupon   
30861             4.752069e+09  2020045209120         Coupon   
30868             4.893630e+09  2020050977988           Loss   
30884             4.945580e+09  2020062726075           Loss   
34998             3.946790e+09  2020057965173           Loss   
41288             4.589242e+09  2020051506877  

In [89]:
df[(df['Name']=='Barro, Joven') & (df['t_activity_day']=='2022-10-31')][cols]

t_ts_created_at t_id_reservation_code_issued  \
44770 2022-10-31 16:53:42+00:00                   HMMHCBSENW   
44771 2022-10-31 16:56:55+00:00                   HMA4FECDES   
44772 2022-10-31 16:57:19+00:00                   HMA4FECDES   
44773 2022-10-31 16:57:43+00:00                   HMA4FECDES   

       t_id_reservation_issued    t_id_ticket t_expense_type  \
44770             4.958967e+09  2020062556383         Coupon   
44771             4.659917e+09  2020060009577           Loss   
44772             4.659917e+09  2020060009577           Loss   
44773             4.659917e+09  2020060009577           Loss   

       t_m_loss_amount_usd  t_m_savings_usd_at_issuance          Name  \
44770                  NaN                  1237.388603  Barro, Joven   
44771              3944.03                          NaN  Barro, Joven   
44772              1531.24                          NaN  Barro, Joven   
44773              1135.48                          NaN  Barro, Joven   

       t_id_airbnb_agent t_id_customer  With_Reservation  \
44770          358262320       3392329                 1   
44771          358262320     372645485                 1   
44772          358262320     372645485                 1   
44773          358262320     372645485                 1   

       abnormal_daily_frequency  agent_customer_same  \
44770                         1                    0   
44771                         1                    0   
44772                         1                    0   
44773                         1                    0   

       abnormal_process_time_interval  suspicious_duplicates  \
44770                               0                    0.0   
44771                               0                    0.0   
44772                               0                    0.0   
44773                               0                    0.0   

       not_reported_3000USD  personal_ID_recepient  suspicious_customer  \
44770                     0                      0                    0   
44771                     1                      0                    0   
44772                     0                      0                    0   
44773                     0                      0                    0   

       prediction_confidence  
44770                    0.0  
44771                    2.0  
44772                    0.0  
44773                    0.0

In [90]:
df[(df['Name']=='Barro, Joven')]['t_activity_day'].value_counts()[:10]

2022-09-05    5
2022-10-31    4
2022-06-23    4
2022-03-31    4
2022-11-12    3
2022-01-27    3
2022-02-10    3
2022-11-08    3
2022-05-18    3
2022-06-07    3
Name: t_activity_day, dtype: int64

In [91]:
df_suspicious[df_suspicious['Name']=='Cayetano, Jhanine'][cols]

t_ts_created_at t_id_reservation_code_issued  \
81571 2022-11-10 06:51:53+00:00                   HMP53Q25CZ   
81572 2022-11-11 08:14:26+00:00                   HM9FHTZ9EP   
81573 2022-11-11 08:14:40+00:00                   HM9FHTZ9EP   
81574 2022-11-11 08:14:51+00:00                   HM9FHTZ9EP   
81575 2022-11-11 08:15:03+00:00                   HM9FHTZ9EP   
81576 2022-11-11 08:15:14+00:00                   HM9FHTZ9EP   
81577 2022-11-11 08:15:28+00:00                   HM9FHTZ9EP   
81578 2022-11-11 08:15:39+00:00                   HM9FHTZ9EP   
81579 2022-11-11 08:15:51+00:00                   HM9FHTZ9EP   
81580 2022-11-11 08:16:02+00:00                   HM9FHTZ9EP   
81581 2022-11-11 08:19:15+00:00                   HM9FHTZ9EP   
81582 2022-11-11 08:24:43+00:00                   HMBFSSBRMY   
81583 2022-11-11 08:27:13+00:00                   HMJZMM3E8Q   
81584 2022-11-11 08:30:24+00:00                   HMTYJ55Z4F   
81585 2022-11-11 08:34:08+00:00                   HMPES9H3SN   
81586 2022-11-11 08:37:10+00:00                   HMNN895EKA   
81587 2022-11-11 08:39:12+00:00                   HMTCEFJJ5D   
81588 2022-11-11 08:41:50+00:00                   HMCFRHQ222   
81589 2022-11-11 08:44:01+00:00                   HMM4KR9QSZ   
81590 2022-11-11 08:45:51+00:00                          NaN   
81591 2022-11-11 08:46:06+00:00                          NaN   
81592 2022-11-11 08:48:17+00:00                   HM4DFEKYR8   
81593 2022-11-11 08:50:26+00:00                   HMXZK3J3SK   
81594 2022-11-12 06:06:37+00:00                   HM8HR9PRDS   
81595 2022-11-12 06:08:55+00:00                   HMSFHJASSH   
81596 2022-11-12 06:11:09+00:00                   HMZEPN8QBQ   
81597 2022-11-12 06:12:52+00:00                   HM9MKQQ2X5   
81598 2022-11-12 06:14:29+00:00                   HMP8PBH2FA   

       t_id_reservation_issued    t_id_ticket t_expense_type  \
81571             4.960594e+09  2020063795411           Loss   
81572             4.969521e+09  2020064005443         Coupon   
81573             4.969521e+09  2020064005443         Coupon   
81574             4.969521e+09  2020064005443         Coupon   
81575             4.969521e+09  2020064005443         Coupon   
81576             4.969521e+09  2020064005443         Coupon   
81577             4.969521e+09  2020064005443         Coupon   
81578             4.969521e+09  2020064005443         Coupon   
81579             4.969521e+09  2020064005443         Coupon   
81580             4.969521e+09  2020064005443         Coupon   
81581             4.969521e+09  2020064005443           Loss   
81582             4.969522e+09  2020064005930           Loss   
81583             4.969522e+09  2020064006105           Loss   
81584             4.969523e+09  2020064006306           Loss   
81585             4.969523e+09  2020064006422           Loss   
81586             4.969524e+09  2020064006663           Loss   
81587             4.969524e+09  2020064006769           Loss   
81588             4.969525e+09  2020064006909           Loss   
81589             4.969525e+09  2020064007040           Loss   
81590                      NaN  2020064007198         Coupon   
81591                      NaN  2020064007198         Coupon   
81592             4.969526e+09  2020064007310           Loss   
81593             4.969526e+09  2020064007446           Loss   
81594             3.941145e+09  2020064126437           Loss   
81595             3.841512e+09  2020064126614           Loss   
81596             3.838025e+09  2020064126706           Loss   
81597             3.830259e+09  2020064126793           Loss   
81598             3.826933e+09  2020064126859           Loss   

       t_m_loss_amount_usd  t_m_savings_usd_at_issuance               Name  \
81571           195.020053                          NaN  Cayetano, Jhanine   
81572                  NaN                         20.0  Cayetano, Jhanine   
81573                  NaN                         20.0  Cayetano, J

In [92]:
reservations_suspicious = ['HMP53Q25CZ', 'HM9FHTZ9EP', 'HMBFSSBRMY',
                           'HMJZMM3E8Q', 'HMTYJ55Z4F', 'HMPES9H3SN',
                           'HMNN895EKA', 'HMTCEFJJ5D', 'HMCFRHQ222',
                           'HMM4KR9QSZ', 'HM4DFEKYR8', 'HMXZK3J3SK',
                           'HM8HR9PRDS', 'HMSFHJASSH', 'HMZEPN8QBQ',
                           'HM9MKQQ2X5', 'HMP8PBH2FA']

In [93]:
df[df['t_id_reservation_code_issued'].isin(reservations_suspicious)][cols].shape

(26, 19)

# Month on Month Transactions

In [94]:
# Check if confirmed fraud cases are flagged by the model


In [95]:
# count = 0
# for customer in customers_id:
#     df_customer = df[df['t.id_customer'] == customer]
 
#     # check how many reservations the customer had made
#     ticket_counts = df_customer['t.id_ticket'].nunique()
#     agent_counts = df_customer['t.id_airbnb_agent'].nunique()
#     if agent_counts == 1:
#         print('Customer ID: ', customer)
#         print('Number of tickets made: ', ticket_counts)
#         print('Number of agents: ', agent_counts)
#         print('--------')
#         display(df_customer[cols])
    
#         count +=1